In [795]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from collections import Counter
import itertools

In [796]:
data = pd.read_csv('movie_bd_v5.csv')
data.sample(5)

imdb_id     budget    revenue            original_title  \
1150  tt0304711   35000000   11560806                 The Order   
91    tt2938956   25000000   72629670  The Transporter Refueled   
1732  tt0423294   85000000  149044513                 Surf's Up   
283   tt0485947   47000000    3547209                Mr. Nobody   
1106  tt0172156  130000000  273339556               Bad Boys II   

                                                                          cast  \
1150       Heath Ledger|Shannyn Sossamon|Benno FÃ¼rmann|Mark Addy|Peter Weller   
91    Ed Skrein|Ray Stevenson|Loan Chabanol|Gabriella Wright|Tatjana PajkoviÄ‡   
1732           Shia LaBeouf|Jeff Bridges|Zooey Deschanel|Jon Heder|James Woods   
283            Jared Leto|Diane Kruger|Linh Äan Pháº¡m|Sarah Polley|Rhys Ifans   
1106    Martin Lawrence|Will Smith|Jordi MollÃ |Gabrielle Union|Peter Stormare   

                    director  \
1150         Brian Helgeland   
91         Camille Delamarre   
1732  Ash Brannon|Chris Buck   
283         Jaco Van Dormael   
1106             Michael Bay   

                                                            tagline  \
1150                                      Every soul has its price.   
91                                                     He Delivers.   
1732  In the coldest place on Earth, he's the hottest thing around.   
283                        Nothing is real, everything is possible.   
1106                 If you can't stand the heat, get out of Miami.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         overview  \
1150                                                                                                                                                                           For centuries, a secret Order of priests has existed within the Church. A renegade priest, Father Alex Bernier, is sent to Rome to investigate the mysterious death of one of the Order's most revered members. Following a series of strangely similar killings, Bernier launches an investigation that forces him to confront unimaginable evil.   
91                                                                                                                                                                             The fast-paced action movie is again set in the criminal underworld in France, where Frank Martin is known as The Transporter, because he is the best driver and mercenary money can buy. In this installment, he meets Anna and they attempt to take down a group of ruthless Russian human traffickers who also have kidnapped Frankâ€™s father.   
1732  Cody is a surfing penguin from Shiverpool who dreams of making it big and being like his idol Big Z. On his journey he discovers his talents are not all he thinks they are and he must learn to accept that their is more to surfing than fame and fortune.  Surf's Up is a 2007 American computer-animated mockumentary film produced by Sony Pictures Animation and distributed by Columbia Pictures and ImageWorks Studios. It stars the voices of Shia LaBeouf, Jeff Bridges, Zooey Deschanel, Jon Heder among others.   
283                                                                                                                                                                                                                                                                                                                                                                                          Nemo Nobody leads an ordinary existence wit

In [4]:
data.columns

Index(['imdb_id', 'budget', 'revenue', 'original_title', 'cast', 'director',
       'tagline', 'overview', 'runtime', 'genres', 'production_companies',
       'release_date', 'vote_average', 'release_year'],
      dtype='object')

In [127]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1889 entries, 0 to 1888
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   imdb_id               1889 non-null   object 
 1   budget                1889 non-null   int64  
 2   revenue               1889 non-null   int64  
 3   original_title        1889 non-null   object 
 4   cast                  1889 non-null   object 
 5   director              1889 non-null   object 
 6   tagline               1889 non-null   object 
 7   overview              1889 non-null   object 
 8   runtime               1889 non-null   int64  
 9   genres                1889 non-null   object 
 10  production_companies  1889 non-null   object 
 11  release_date          1889 non-null   object 
 12  vote_average          1889 non-null   float64
 13  release_year          1889 non-null   int64  
dtypes: float64(1), int64(4), object(9)
memory usage: 206.7+ KB


In [37]:
data.style.format({'budget': "{:,d}", 'revenue': '{:,d}'})

In [826]:
data.nunique()

imdb_id                 1889
budget                   203
revenue                 1885
original_title          1887
cast                    1878
director                 957
tagline                 1880
overview                1889
runtime                  105
genres                   652
production_companies    1624
release_date            1435
vote_average              47
release_year              16
dtype: int64

In [855]:
# Find films which have two equal names.
data.original_title.groupby(data.original_title).count().sort_values(ascending=False)

original_title
Fantastic Four                       2
The Gift                             2
Hop                                  1
High Fidelity                        1
Highlander: Endgame                  1
                                    ..
Spy                                  1
Spy Game                             1
Spy Kids                             1
Spy Kids 2: Island of Lost Dreams    1
(500) Days of Summer                 1
Name: original_title, Length: 1887, dtype: int64

In [859]:
data.query("original_title == 'Fantastic Four'").release_year
# In 2015 there was new release of the same story about fantastic four with different directors and cast.
# In principle we can give different names by adding a release year (if it will be needed for some questions further).

55      2015
1322    2005
Name: release_year, dtype: int64

In [860]:
data.query("original_title == 'The Gift'").release_year
# These are two different movie stories but with the same naming.
# In principle we can give different names by adding a release year (if it will be needed for some questions further).

75      2015
1834    2000
Name: release_year, dtype: int64

# Предобработка

In [914]:
answers = {} # Create dictionary for answers

# 1. Change release_date format.
# release_date given in the dataset is in string format. Changing to datetime format.
data['release_date'] = data['release_date'].astype('datetime64')
data['release_date'].dt.month # checking

# 2. Create new column "profit" = "revenue" - "budget".
data['profit'] = data['revenue'] - data['budget']

# 3. Create new dataframes with separate genres, actors, directors, production_companies.

"""Create function that converts a string with many elements
dividing by | to a list with these elements"""

def list_of_elements(s):
    return s.split(sep='|')
   
    
""" Create function that returns dictionary where
 keys = genres/actors/.., 
 values = 1 if this genre/actor/.. is in current row of df, 
 and 0 if this genre/actor/.. is not in current row of df."""

def get_dict_of_elements(element_list_of_list, df_row_count): 
    # df_row_count = length of original dataframe
    g_dict = {} 
    for element_list in element_list_of_list:
        for key in element_list:
            # For each key creating list with 0 values, lenght = Qty of df rows
            g_dict[key] = [0] * df_row_count 

    for key, value in g_dict.items(): 
        enum = enumerate(element_list_of_list)
        for row_num, element_list in enum:
            if key in element_list:
                # Fill dict with elements-keys, values = numbers of rows, where these elements are.
                value[row_num] = 1       
          
    return g_dict


# Create new dataframe with columns: imdb_id and all genres 
# and cells = 1 if film in this genre and 0 if film not is this genre
genre_list_of_list = data.genres.apply(list_of_elements)  
dict_of_genres = get_dict_of_elements(genre_list_of_list, len(data.index))

film_genre = pd.DataFrame(dict_of_genres)
film_genre.insert(loc=0, column='imdb_id', value=data.imdb_id)

# Create new dataframe with columns: imdb_id and all actors
# and cells = 1 if actor played in this film and 0 if didn't play
cast_list_of_list = data.cast.apply(list_of_elements) 
dict_of_cast = get_dict_of_elements(cast_list_of_list, len(data.index))

film_cast = pd.DataFrame(dict_of_cast)
film_cast.insert(loc=0, column='imdb_id', value=data.imdb_id)

# Create new dataframe with columns: imdb_id and all directors
# and cells = 1 if director made this film and 0 if he didn't
director_list_of_list = data.director.apply(list_of_elements)  
dict_of_directors = get_dict_of_elements(director_list_of_list, len(data.index))

film_director = pd.DataFrame(dict_of_directors)
film_director.insert(loc=0, column='imdb_id', value=data.imdb_id)

# Create new dataframe with columns: imdb_id and all production_companies
# and cells = 1 if current production_company made this film and 0 if it didn't
production_list_of_list = data.production_companies.apply(list_of_elements)  
dict_of_production = get_dict_of_elements(production_list_of_list, len(data.index))

film_production = pd.DataFrame(dict_of_production)
film_production.insert(loc=0, column='imdb_id', value=data.imdb_id)
film_production

imdb_id  Universal Studios  Amblin Entertainment  Legendary Pictures  \
0     tt0369610                  1                     1                   1   
1     tt1392190                  0                     0                   0   
2     tt2908446                  0                     0                   0   
3     tt2488496                  0                     0                   0   
4     tt2820852                  0                     0                   0   
...         ...                ...                   ...                 ...   
1884  tt0120903                  0                     0                   0   
1885  tt0192255                  0                     0                   0   
1886  tt0131704                  0                     0                   0   
1887  tt0162983                  0                     0                   0   
1888  tt0163676                  0                     0                   0   

      Fuji Television Network  Dentsu  Village Roadshow Pictures  \
0                           1       1                          0   
1                           0       0                          1   
2                           0       0                          0   
3                           0       0                          0   
4                           0       1                          0   
...                       ...     ...                        ...   
1884                        0       0                          0   
1885                        0       0                          0   
1886                        0       0                          0   
1887                        0       0                          0   
1888                        0       0                          0   

      Kennedy Miller Productions  Summit Entertainment  Mandeville Films  ...  \
0                              0                     0                 0  ...   
1                              1                     0                 0  ...   
2                              0                     1                 1  ...   
3                              0                     0                 0  ...   
4                              0                     0                 0  ...   
...                          ...                   ...               ...  ...   
1884                           0                     0                 0  ...   
1885                           0                     0                 0  ...   
1886                           0                     0                 0  ...   
1887                           0                     0                 0  ...   
1888                           0                     0                 0  ...   

      Walrus & Associates  Hollywood Partners  Charenton Productions  \
0                       0                   0                      0   
1                       0                   0                      0   
2                       0                   0                      0   
3                       0                   0                      0   
4                       0                   0                      0   
...                   ...                 ...                    ...   
1884                    0                   0                      0   
1885                    0                   0                      0   
1886                    0                   0                      0   
1887                    0                   0                      0   
1888                    0                   0                      0   

      Sweetpea Entertainment  SNL Studios  JLT Productions  \
0                          0            0                0   
1                          0            0                0   
2                          0            0                0   
3                          0            0                0   
4                          0            0                0   
...                 

# 1. У какого фильма из списка самый большой бюджет?

Использовать варианты ответов в коде решения запрещено.    
Вы думаете и в жизни у вас будут варианты ответов?)

In [915]:
answers['1'] = '723. Pirates of the Caribbean: On Stranger Tides (tt0413300)'
# +

In [124]:
data.loc[data['budget'] == data['budget'].max()][['imdb_id','original_title']]

imdb_id                               original_title
723  tt1298650  Pirates of the Caribbean: On Stranger Tides

ВАРИАНТ 2

In [144]:
# Other two variants of solving question 1.
data.sort_values(by='budget', ascending=False)[['imdb_id','original_title']].iloc[0]
data.query('budget == budget.max()').original_title

imdb_id                                             tt1298650
original_title    Pirates of the Caribbean: On Stranger Tides
Name: 723, dtype: object

# 2. Какой из фильмов самый длительный (в минутах)?

In [916]:
answers['2'] = '1157. Gods and Generals (tt0279111)'
# +

In [145]:
data.sort_values(by='runtime', ascending=False)[['imdb_id','original_title']].iloc[0] # Variant 1
data.query('runtime == runtime.max()').original_title # Variant 2

1157    Gods and Generals
Name: original_title, dtype: object

# 3. Какой из фильмов самый короткий (в минутах)?





In [917]:
answers['3'] = '768. Winnie the Pooh (tt449283)'
# +

In [146]:
data.loc[data['runtime'] == data['runtime'].min()][['imdb_id','original_title']]

imdb_id   original_title
768  tt1449283  Winnie the Pooh

In [149]:
# Other 2 variants of solving question 3.
data.sort_values(by='runtime')[['imdb_id','original_title']].iloc[0]
data.query('runtime == runtime.min()').original_title

768    Winnie the Pooh
Name: original_title, dtype: object

# 4. Какова средняя длительность фильмов?


In [918]:
answers['4'] = '110'
# +

In [160]:
data['runtime'].mean()

109.6585494970884

# 5. Каково медианное значение длительности фильмов? 

In [919]:
answers['5'] = '107'
# +

In [161]:
data.runtime.median()

107.0

# 6. Какой самый прибыльный фильм?
#### Внимание! Здесь и далее под «прибылью» или «убытками» понимается разность между сборами и бюджетом фильма. (прибыль = сборы - бюджет) в нашем датасете это будет (profit = revenue - budget) 

In [920]:
answers['6'] = '239. Avatar (tt0499549)'
# +

In [169]:
data.loc[data['profit'] == data['profit'].max()][['imdb_id','original_title']]

imdb_id original_title
239  tt0499549         Avatar

# 7. Какой фильм самый убыточный? 

In [921]:
answers['7'] = '1245. The Lone Ranger (tt1210819)'
# +

In [173]:
data.query('profit == profit.min()')[['imdb_id','original_title']]

imdb_id   original_title
1245  tt1210819  The Lone Ranger

# 8. У скольких фильмов из датасета объем сборов оказался выше бюджета?

In [922]:
answers['8'] = '1478'
# +

In [181]:
data.query('profit > 0').profit.count()

1478

# 9. Какой фильм оказался самым кассовым в 2008 году?

In [923]:
answers['9'] = '599. The Dark Knight (tt0468569)'
# +

In [197]:
data.query('release_year == 2008').sort_values(by='profit', ascending=False)[['imdb_id','original_title']].iloc[0]

imdb_id                 tt0468569
original_title    The Dark Knight
Name: 599, dtype: object

# 10. Самый убыточный фильм за период с 2012 по 2014 г. (включительно)?


In [924]:
answers['10'] = '1245. The Lone Ranger (tt1210819)'
# +

In [200]:
data.query('2012 <= release_year <= 2014').sort_values(by='profit')[['imdb_id','original_title']].iloc[0]

imdb_id                 tt1210819
original_title    The Lone Ranger
Name: 1245, dtype: object

# 11. Какого жанра фильмов больше всего?

In [984]:
answers['11'] = 'Drama'
# +

In [581]:
# Сreating of new df "film_genre" is in block of data preprocessing.
film_genre.loc[:, film_genre.columns != 'imdb_id'].sum().sort_values(ascending=False)

Drama              782
Comedy             683
Thriller           596
Action             582
Adventure          415
Crime              315
Romance            308
Family             260
Science Fiction    248
Fantasy            222
Horror             176
Mystery            168
Animation          139
Music               64
History             62
War                 58
Western             19
Documentary          8
Foreign              2
dtype: int64

ВАРИАНТ 2

In [467]:
# Second variant.
film_genre.drop('imdb_id', axis=1).sum().idxmax()

'Drama'

In [947]:
# Variant without stack method.
genres_df = pd.DataFrame(data['genres'].str.split('|').tolist())
genres_df.stack().value_counts()

Drama              782
Comedy             683
Thriller           596
Action             582
Adventure          415
Crime              315
Romance            308
Family             260
Science Fiction    248
Fantasy            222
Horror             176
Mystery            168
Animation          139
Music               64
History             62
War                 58
Western             19
Documentary          8
Foreign              2
dtype: int64

# 12. Фильмы какого жанра чаще всего становятся прибыльными? 

In [987]:
answers['12'] = 'Drama'
# +

In [579]:
data_profit = data[data.profit > 0]
# Сreating of new df "film_genre" is in block of data preprocessing.
# We merge new df film_genre to column "profit".
genre_profit = data_profit[['imdb_id','profit']].merge(film_genre, on='imdb_id', how='left')
genre_profit.drop(['imdb_id','profit'], axis=1).sum().sort_values(ascending=False).idxmax()

'Drama'

In [948]:
# Variant without stack method.
data_profit = data[data.profit > 0]
genres_profit_df = pd.DataFrame(data_profit['genres'].str.split('|').tolist())
genres_profit_df.stack().value_counts()

Drama              560
Comedy             551
Thriller           446
Action             444
Adventure          337
Romance            242
Crime              231
Family             226
Science Fiction    195
Fantasy            188
Horror             150
Animation          120
Mystery            119
Music               47
History             46
War                 41
Western             12
Documentary          7
dtype: int64

# 13. У какого режиссера самые большие суммарные кассовые сборы?

In [988]:
answers['13'] = 'Peter Jackson'
# +

In [267]:
data.groupby('director').revenue.sum().sort_values(ascending=False).head(1)

director
Peter Jackson    6490593685
Name: revenue, dtype: int64

In [532]:
# Variant 2 by creating of new df "film_director" (is in block of data preprocessing).
# Create df with directors and their revenue.
director_revenue = film_director.merge(data[['imdb_id','revenue']], on='imdb_id', how='left')
# Multiply values (1 or 0) in df on values of revenue column.
dr = director_revenue.drop(['imdb_id','revenue'], axis=1).mul(director_revenue.revenue, axis=0)
dr.sum().sort_values(ascending=False).idxmax()

'Peter Jackson'

# 14. Какой режиcсер снял больше всего фильмов в стиле Action?

In [989]:
answers['14'] = 'Robert Rodriguez'
# +

In [512]:
# Сreating of new df "film_director" is in block of data preprocessing.
# Create df with directors who made films only in Action genre.
Action_director = film_director.merge(film_genre[['imdb_id','Action']], on='imdb_id', how='left')
Action_director.query('Action == 1').drop(['imdb_id','Action'], axis=1).sum().idxmax()

'Robert Rodriguez'

# 15. Фильмы с каким актером принесли самые высокие кассовые сборы в 2012 году? 

In [990]:
answers['15'] = 'Chris Hemsworth'
# +

In [534]:
pd.set_option('display.max_colwidth', None) # the maximum width of each single field
data.query('release_year == 2012').sort_values(by='revenue', ascending=False)[['cast']].iloc[0]
# not clear variant

cast    Robert Downey Jr.|Chris Evans|Mark Ruffalo|Chris Hemsworth|Scarlett Johansson
Name: 970, dtype: object

In [549]:
# Variant 2 with creating of new df "film_cast" (is in block of data preprocessing).
data_2012 = data.query('release_year == 2012') # taking only 2012 year
# Create df with cast and their revenue.
cast_revenue = data_2012[['imdb_id','revenue']].merge(film_cast, on='imdb_id', how='left')
cast = cast_revenue.drop(['imdb_id','revenue'], axis=1).mul(cast_revenue.revenue, axis=0)
cast.sum().sort_values(ascending=False).idxmax()

'Chris Hemsworth'

# 16. Какой актер снялся в большем количестве высокобюджетных фильмов?

In [991]:
answers['16'] = 'Matt Damon'
# +

In [556]:
# Creating of new df "film_cast" is in block of data preprocessing.
high_budget = data.query('budget >= budget.mean()') # get films with high budget
cast_budget = high_budget[['imdb_id','budget']].merge(film_cast, on='imdb_id', how='left')
cast_budget.drop(['imdb_id','budget'], axis=1).sum().sort_values(ascending=False).idxmax()

'Matt Damon'

In [961]:
# Variant 2 with stack method.
high_budget = data.query('budget >= budget.mean()')
cast_budget_df = pd.DataFrame(high_budget['cast'].str.split('|').tolist())
cast_budget_df.stack().value_counts()

Matt Damon           18
Adam Sandler         17
Angelina Jolie       16
Samuel L. Jackson    15
Eddie Murphy         15
                     ..
Randy Couture         1
Iain Glen             1
Tommy Flanagan        1
Brooklyn Decker       1
Henry Winkler         1
Length: 1505, dtype: int64

# 17. В фильмах какого жанра больше всего снимался Nicolas Cage? 

In [992]:
answers['17'] = 'Action'
# +

In [570]:
# Creating of new df "film_genre" and "film_cast" is in block of data preprocessing.
# Ceate df with Nicolas Cage film genres.
NC_genre = film_genre.merge(film_cast[['imdb_id','Nicolas Cage']], on='imdb_id', how='left')
NC = NC_genre[NC_genre['Nicolas Cage'] == 1].drop(['imdb_id','Nicolas Cage'], axis=1)
NC.sum().sort_values(ascending=False).idxmax()

'Action'

# 18. Самый убыточный фильм от Paramount Pictures

In [993]:
answers['18'] = '925. K-19: The Widowmaker (tt0267626)'

In [288]:
data.query("production_companies == 'Paramount Pictures'").sort_values('profit')['original_title'].head(3)
# wrong because of different production companies names.

587    Domestic Disturbance
436             The Fighter
961            Serving Sara
Name: original_title, dtype: object

In [582]:
data.loc[data.production_companies.str.contains('Paramoun')].sort_values('profit')['original_title'].head(1)

925    K-19: The Widowmaker
Name: original_title, dtype: object

# 19. Какой год стал самым успешным по суммарным кассовым сборам?

In [994]:
answers['19'] = '2015'
# +

In [296]:
data.groupby('release_year')['revenue'].sum().sort_values(ascending=False).head(1)

release_year
2015    25449202382
Name: revenue, dtype: int64

# 20. Какой самый прибыльный год для студии Warner Bros?

In [995]:
answers['20'] = '2014'
# +

In [315]:
# Make dataframe only with Warner Bros company.
WB = data[data.production_companies.str.contains('Warner Bros')]
# Group by years with sum profit.
WB.groupby('release_year')['profit'].sum().sort_values(ascending=False).head(1)

release_year
2014    2295464519
Name: profit, dtype: int64

# 21. В каком месяце за все годы суммарно вышло больше всего фильмов?

In [996]:
answers['21'] = 'Сентябрь'
# +

In [316]:
data['release_date'].dt.month.value_counts()

9     227
12    190
10    186
8     161
3     156
4     149
6     147
11    146
7     142
5     140
2     135
1     110
Name: release_date, dtype: int64

# 22. Сколько суммарно вышло фильмов летом? (за июнь, июль, август)

In [997]:
answers['22'] = '450'
# +

In [328]:
data.query('6 <= release_date.dt.month <= 8')['imdb_id'].nunique()

450

# 23. Для какого режиссера зима – самое продуктивное время года? 

In [998]:
answers['23'] = 'Peter Jackson'
# +

In [588]:
# Vaiant 1 with creating of new df "film_director" (is in block of data preprocessing).
winter = data.query('(11 <= release_date.dt.month <= 12) | (release_date.dt.month == 1)')
winter_director = winter[['imdb_id','release_date']].merge(film_director, on='imdb_id', how='left')
winter_director.drop(['imdb_id','release_date'], axis=1).sum().sort_values(ascending=False).idxmax()

'Peter Jackson'

In [969]:
# Variant 2 with stack method.
winter = data.query('(11 <= release_date.dt.month <= 12) | (release_date.dt.month == 1)')
winter_director_df = pd.DataFrame(winter['director'].str.split('|').tolist())
winter_director_df.stack().value_counts()

Peter Jackson        8
Clint Eastwood       7
Steven Soderbergh    6
Edward Zwick         4
Robert Zemeckis      4
                    ..
Troy Duffy           1
David Frankel        1
Roger Michell        1
Joseph Kosinski      1
Simon J. Smith       1
Length: 371, dtype: int64

# 24. Какая студия дает самые длинные названия своим фильмам по количеству символов?

In [999]:
answers['24'] = 'Four By Two Productions'
# +

In [606]:
# Variant 1.
# Create new column "title_length" in data.
data['title_length'] = data.original_title.apply(lambda title: len(title)) 
# Use groupby to get maximum title_lenght.
data.groupby(['production_companies']).title_length.max().sort_values(ascending=False).head(1)

production_companies
Twentieth Century Fox Film Corporation|Four By Two Productions    83
Name: title_length, dtype: int64

In [975]:
# Vaiant 2 with creating of new df "film_production" (is in block of data preprocessing).
data['title_length'] = data.original_title.apply(lambda title: len(title)) 
production_title = film_production.merge(data[['imdb_id','title_length']], on='imdb_id', how='left')
production_title_length = production_title.drop(['imdb_id','title_length'], axis=1)\
.mul(production_title.title_length, axis=0) # Multiply values (1 or 0) in df on values of title_length column.
production_title_length.max().sort_values(ascending=False)

Twentieth Century Fox Film Corporation    83
Four By Two Productions                   83
Walt Disney                               62
Walden Media                              62
21 Laps Entertainment                     59
                                          ..
Everest Entertainment                      3
Berlanti Productions                       3
Global Entertainment Group                 2
XM2 Productions                            2
Ixtlan Productions                         2
Length: 1771, dtype: int64

# 25. Описание фильмов какой студии в среднем самые длинные по количеству слов?

In [1000]:
answers['25'] = 'Midnight Picture Show'
# +

In [610]:
# Create function that calculate quantity of words in film description.

def word_qty(s):
    word_list = s.split(sep=' ')
    return len(word_list)

# Add new column applying function.
data['overview_length'] = data.overview.apply(word_qty)
data.groupby(['production_companies']).overview_length.mean().sort_values(ascending=False)

production_companies
Lions Gate Films|Lakeshore Entertainment|GreeneStreet Films|Midnight Picture Show                                 175
Paramount Pictures|Metro-Goldwyn-Mayer (MGM)|Radical Studios|Flynn Picture Company                                169
Village Roadshow Pictures|NPV Entertainment|Heineken Branded Entertainment|Silver Pictures|Warner Bros.           161
Fox Searchlight Pictures|Room 9 Entertainment                                                                     161
Columbia Pictures|Revolution Studios|Happy Madison Productions                                                    159
                                                                                                                 ... 
Focus Films                                                                                                        12
Cheyenne Enterprises|Epsilon Motion Pictures|Empire Pictures|Metro-Goldwyn-Mayer (MGM)|Hyde Park Entertainment     11
Motion Picture Corporation of Ameri

In [627]:
# Variant 2 (more clear).

def word_qty(s):
    word_list = s.split(sep=' ')
    return len(word_list)

# Add new column applying function.
data['overview_length'] = data.overview.apply(word_qty)

# Make new DF of production companies with film overview.
# Creating of new df "film_production" is in block of data preprocessing.

production_overview = film_production.merge(data[['imdb_id', 'overview_length']], on='imdb_id', how='left')
po = production_overview.drop(['imdb_id','overview_length'], axis=1).mul(production_overview.overview_length, axis=0)
po = po.replace(0, np.nan)  # Replace 0 to nan to get mean value of word length in overview.
po.mean().sort_values(ascending=False).head(1)

Midnight Picture Show    175
dtype: float64

# 26. Какие фильмы входят в 1 процент лучших по рейтингу? 
по vote_average

In [1001]:
answers['26'] = 'The Dark Knight, Inside Out, 12 Years a Slave'
# +

In [978]:
# Variant 1 with np.percebtile method.
data[data.vote_average > np.percentile(data.vote_average, 99)].original_title

9                                          Inside Out
34                                               Room
118                                      Interstellar
119                           Guardians of the Galaxy
125                                The Imitation Game
128                                         Gone Girl
138                          The Grand Budapest Hotel
370                                         Inception
599                                   The Dark Knight
872                                       The Pianist
1081    The Lord of the Rings: The Return of the King
1183                          The Wolf of Wall Street
1191                                 12 Years a Slave
1800                                          Memento
Name: original_title, dtype: object

In [979]:
# Variant 2: df.quantile method with decreasing vote_average.
data[data.vote_average > data.quantile(0.99)['vote_average']].\
sort_values(by='vote_average', ascending=False).original_title

599                                   The Dark Knight
9                                          Inside Out
34                                               Room
118                                      Interstellar
125                                The Imitation Game
119                           Guardians of the Galaxy
128                                         Gone Girl
138                          The Grand Budapest Hotel
370                                         Inception
872                                       The Pianist
1081    The Lord of the Rings: The Return of the King
1183                          The Wolf of Wall Street
1191                                 12 Years a Slave
1800                                          Memento
Name: original_title, dtype: object

# 27. Какие актеры чаще всего снимаются в одном фильме вместе?


In [1002]:
answers['27'] = 'Daniel Radcliffe & Rupert Grint'
# +

In [789]:
cast_list_of_lists = data['cast'].str.split('|').tolist() # List with lists of actors.
comb_list_of_lists = []

for lists in cast_list_of_lists:
    comb = list(itertools.combinations(lists, 2)) # Make a list with combination actor pairs.
    comb_list_of_lists.append(comb) # Fill total list of lists combination pairs.
    
merged = list(itertools.chain.from_iterable(comb_list_of_lists)) # Merged list of combination pairs  
Counter(merged).most_common(5)

[(('Daniel Radcliffe', 'Rupert Grint'), 8),
 (('Daniel Radcliffe', 'Emma Watson'), 8),
 (('Rupert Grint', 'Emma Watson'), 7),
 (('Ben Stiller', 'Owen Wilson'), 6),
 (('Johnny Depp', 'Helena Bonham Carter'), 6)]

# Submission

In [1003]:
answers

{'1': '723. Pirates of the Caribbean: On Stranger Tides (tt0413300)',
 '2': '1157. Gods and Generals (tt0279111)',
 '3': '768. Winnie the Pooh (tt449283)',
 '4': '110',
 '5': '107',
 '6': '239. Avatar (tt0499549)',
 '7': '1245. The Lone Ranger (tt1210819)',
 '8': '1478',
 '9': '599. The Dark Knight (tt0468569)',
 '10': '1245. The Lone Ranger (tt1210819)',
 '12': 'Drama',
 '13': 'Peter Jackson',
 '14': 'Robert Rodriguez',
 '15': 'Chris Hemsworth',
 '16': 'Matt Damon',
 '17': 'Action',
 '18': '925. K-19: The Widowmaker (tt0267626)',
 '19': '2015',
 '20': '2014',
 '21': 'Сентябрь',
 '22': '450',
 '23': 'Peter Jackson',
 '24': 'Four By Two Productions',
 '25': 'Midnight Picture Show',
 '26': 'The Dark Knight, Inside Out, 12 Years a Slave',
 '27': 'Daniel Radcliffe & Rupert Grint',
 '11': 'Drama'}

In [1004]:
len(answers)

27